## Please input your directory for the top level folder
folder name : SUBMISSION MODEL

In [14]:
dir_ = 'E:/Seminararbeit/Code/A1/' # input only here

#### setting other directory

In [15]:
raw_data_dir = dir_+'2. data/'
processed_data_dir = dir_+'2. data/processed/'
log_dir = dir_+'4. logs/'
model_dir = dir_+'5. models/'

In [16]:
####################################################################################
#################### 2-2. nonrecursive model by store & cat ########################
####################################################################################

In [17]:
cvs = ['private']

In [18]:
STORES = ['CA_1', 'CA_2', 'CA_3', 'CA_4', 'TX_1', 'TX_2', 'TX_3', 'WI_1', 'WI_2', 'WI_3'] 
CATS = ['FOODS'] #'HOBBIES', 'HOUSEHOLD', 'FOODS'

In [19]:
from  datetime import datetime, timedelta
import gc
import numpy as np, pandas as pd
import lightgbm as lgb

import os, sys, gc, time, warnings, pickle, psutil, random

warnings.filterwarnings('ignore')

In [20]:
def reduce_mem_usage(df, verbose=False):
    numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
    start_mem = df.memory_usage().sum() / 1024**2    
    for col in df.columns:
        col_type = df[col].dtypes
        if col_type in numerics:
            c_min = df[col].min()
            c_max = df[col].max()
            if str(col_type)[:3] == 'int':
                if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
                    df[col] = df[col].astype(np.int8)
                elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
                       df[col] = df[col].astype(np.int16)
                elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
                    df[col] = df[col].astype(np.int32)
                elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
                    df[col] = df[col].astype(np.int64)  
            else:
                if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
                    df[col] = df[col].astype(np.float16)
                elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
                    df[col] = df[col].astype(np.float32)
                else:
                    df[col] = df[col].astype(np.float64)    
    end_mem = df.memory_usage().sum() / 1024**2
    if verbose: print('Mem. usage decreased to {:5.2f} Mb ({:.1f}% reduction)'.format(end_mem, 100 * (start_mem - end_mem) / start_mem))
    return df

In [21]:
FIRST_DAY = 710 
remove_feature = ['id',
                  'state_id',
                  'store_id',
#                   'item_id',
#                   'dept_id',
                  'cat_id',
                  'date','wm_yr_wk','d','sales']

cat_var = ['item_id', 'dept_id','store_id', 'cat_id', 'state_id'] + ["event_name_1", "event_name_2", "event_type_1", "event_type_2"]
cat_var = list(set(cat_var) - set(remove_feature))

In [22]:
grid2_colnm = ['sell_price', 'price_max', 'price_min', 'price_std',
               'price_mean', 'price_norm', 'price_nunique', 'item_nunique',
               'price_momentum', 'price_momentum_m', 'price_momentum_y']

grid3_colnm = ['event_name_1', 'event_type_1', 'event_name_2',
               'event_type_2', 'snap_CA', 'snap_TX', 'snap_WI', 'tm_d', 'tm_w', 'tm_m',
               'tm_y', 'tm_wm', 'tm_dw', 'tm_w_end']

lag_colnm = [ 'sales_lag_28', 'sales_lag_29', 'sales_lag_30',
             'sales_lag_31', 'sales_lag_32', 'sales_lag_33', 'sales_lag_34',
             'sales_lag_35', 'sales_lag_36', 'sales_lag_37', 'sales_lag_38',
             'sales_lag_39', 'sales_lag_40', 'sales_lag_41', 'sales_lag_42',
             
             'rolling_mean_7', 'rolling_std_7', 'rolling_mean_14', 'rolling_std_14',
             'rolling_mean_30', 'rolling_std_30', 'rolling_mean_60',
             'rolling_std_60', 'rolling_mean_180', 'rolling_std_180']

mean_enc_colnm = [
    
    'enc_store_id_dept_id_mean', 'enc_store_id_dept_id_std', 
    'enc_item_id_store_id_mean', 'enc_item_id_store_id_std'

]

In [23]:
########################### Make grid
#################################################################################
def prepare_data(store, state):
    
    grid_1 = pd.read_pickle(processed_data_dir+"processedgrid_part_1.pkl")
    grid_2 = pd.read_pickle(processed_data_dir+"processedgrid_part_2.pkl")[grid2_colnm]
    grid_3 = pd.read_pickle(processed_data_dir+"processedgrid_part_3.pkl")[grid3_colnm]

    grid_df = pd.concat([grid_1, grid_2, grid_3], axis=1)
    del grid_1, grid_2, grid_3; gc.collect()
    
    grid_df = grid_df[(grid_df['store_id'] == store) & (grid_df['cat_id'] == state)]
    grid_df = grid_df[grid_df['d'] >= FIRST_DAY]
    
    lag = pd.read_pickle(processed_data_dir+"processedlags_df_28.pkl")[lag_colnm]
    
    lag = lag[lag.index.isin(grid_df.index)]
    
    grid_df = pd.concat([grid_df,
                     lag],
                    axis=1)
    
    del lag; gc.collect()
    

    mean_enc = pd.read_pickle(processed_data_dir+"processedmean_encoding_df.pkl")[mean_enc_colnm]
    mean_enc = mean_enc[mean_enc.index.isin(grid_df.index)]
    
    grid_df = pd.concat([grid_df,
                         mean_enc],
                        axis=1)    
    del mean_enc; gc.collect()
    
    grid_df = reduce_mem_usage(grid_df)
    
    
    
    return grid_df

In [24]:
validation = {
    'cv1' : [1551, 1610],
    'cv2' : [1829,1857],
    'cv3' : [1857, 1885],
    'cv4' : [1885,1913],
    'public' : [1913, 1941],
    'private' : [1941, 1969]
}

### cv1 : 2015-04-28 ~ 2015-06-26

### cv2 : 2016-02-01 ~ 2016-02-28

### cv3 : 2016-02-29 ~ 2016-03-27

### cv4 : 2016-03-28 ~ 2016-04-24

In [25]:
########################### Model params
#################################################################################
lgb_params = {
                    'boosting_type': 'gbdt',
                    'objective': 'tweedie',
                    'tweedie_variance_power': 1.1,
                    'metric': 'rmse',
                    'subsample': 0.5,
                    'subsample_freq': 1,
                    'learning_rate': 0.015,
                    'num_leaves': 2**8-1,
                    'min_data_in_leaf': 2**8-1,
                    'feature_fraction': 0.5,
                    'max_bin': 100,
                    'n_estimators': 3000,
                    'boost_from_average': False,
                    'verbose': 2,
                    'seed' : 1995,
                    'n_jobs': 1
                } 

In [26]:
########################### Train Models
#################################################################################

rmsse_bycv = dict()

for cv in cvs:
    print('cv : day', validation[cv])
    
    pred_list = []
    for store in STORES:
        for state in CATS:

            print(store,state, 'start')
            grid_df = prepare_data(store, state)
            print(grid_df.__sizeof__())
            model_var = grid_df.columns[~grid_df.columns.isin(remove_feature)]

            tr_mask = (grid_df['d'] <= validation[cv][0]) & (grid_df['d'] >= FIRST_DAY)
            vl_mask = (grid_df['d'] > validation[cv][0]) & (grid_df['d'] <= validation[cv][1])

            train_data = lgb.Dataset(grid_df[tr_mask][model_var], 
                           label=grid_df[tr_mask]['sales'])
            print(tr_mask.__sizeof__())
            valid_data = lgb.Dataset(grid_df[vl_mask][model_var], 
                               label=grid_df[vl_mask]['sales'])
            print(vl_mask.__sizeof__())
            
            m_lgb = lgb.train(lgb_params, train_data, valid_sets = [valid_data, train_data], callbacks=[lgb.log_evaluation(1, True)]) 
            model_name = model_dir+'non_recur_model_'+store+'_'+state+'.bin'
            pickle.dump(m_lgb, open(model_name, 'wb'))
            
            display(pd.DataFrame({'name':m_lgb.feature_name(),
                                  'imp':m_lgb.feature_importance()}).sort_values('imp',ascending=False).head(25))
            
            del grid_df, train_data, valid_data, m_lgb, tr_mask, vl_mask; gc.collect

cv : day [1941, 1969]
CA_1 FOODS start
195125863
15049116
15049116
[LightGBM] [Warning] Categorical features with more bins than the configured maximum bin number found.
[LightGBM] [Warning] For categorical features, max_bin and max_bin_by_feature may be ignored with a large number of categories.
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.838417
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.295478
[LightGBM] [Debug] init for col-wise cost 0.069145 seconds, init for row-wise cost 0.947567 seconds
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 1.089651 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 5353
[LightGBM] [Info] Number of data points in the train set: 1631888, number of used features: 57
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Debug] Re-bagging, using 817536 data to train
[LightGBM] [Debug] Trained a tree with leaves = 255 an

name     imp
0                     item_id  136114
22                       tm_w   38241
14               event_name_1   31583
51           rolling_mean_180   27196
52            rolling_std_180   25571
49            rolling_mean_60   23952
12           price_momentum_m   23027
50             rolling_std_60   22417
48             rolling_std_30   19552
21                       tm_d   17220
47            rolling_mean_30   17110
44              rolling_std_7   16505
23                       tm_m   16038
46             rolling_std_14   15629
43             rolling_mean_7   14771
45            rolling_mean_14   14435
13           price_momentum_y   13813
10               item_nunique   12978
6                   price_std   11299
56   enc_item_id_store_id_std   11203
24                       tm_y   11013
28               sales_lag_28   10976
8                  price_norm   10807
55  enc_item_id_store_id_mean   10586
42               sales_lag_42   10498

CA_2 FOODS start
167138543
12858804
12858804
[LightGBM] [Warning] Categorical features with more bins than the configured maximum bin number found.
[LightGBM] [Warning] For categorical features, max_bin and max_bin_by_feature may be ignored with a large number of categories.
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.826520
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.322883
[LightGBM] [Debug] init for col-wise cost 0.089960 seconds, init for row-wise cost 0.844651 seconds
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.185946 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Debug] Using Sparse Multi-Val Bin
[LightGBM] [Info] Total Bins 4938
[LightGBM] [Info] Number of data points in the train set: 1388520, number of used features: 57
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Debug] Re-ba

name     imp
0                     item_id  135858
22                       tm_w   36178
14               event_name_1   32423
51           rolling_mean_180   27795
52            rolling_std_180   25676
49            rolling_mean_60   24083
50             rolling_std_60   23567
12           price_momentum_m   22113
48             rolling_std_30   21061
21                       tm_d   19488
44              rolling_std_7   18649
47            rolling_mean_30   17693
46             rolling_std_14   17401
45            rolling_mean_14   15693
43             rolling_mean_7   14888
23                       tm_m   14647
10               item_nunique   12773
13           price_momentum_y   12603
56   enc_item_id_store_id_std   12481
6                   price_std   11702
55  enc_item_id_store_id_mean   11426
8                  price_norm   10361
3                  sell_price   10232
26                      tm_dw   10215
42               sales_lag_42    9919

CA_3 FOODS start
195348618
15066549
15066549
[LightGBM] [Warning] Categorical features with more bins than the configured maximum bin number found.
[LightGBM] [Warning] For categorical features, max_bin and max_bin_by_feature may be ignored with a large number of categories.
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.837104
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.268831
[LightGBM] [Debug] init for col-wise cost 0.071200 seconds, init for row-wise cost 0.967440 seconds
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 1.106709 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 5366
[LightGBM] [Info] Number of data points in the train set: 1633825, number of used features: 57
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Debug] Re-bagging, using 818501 data to train
[LightGBM] [Debug] Trained a tree with leaves = 255 and depth = 14
[1]	train

...

name     imp
0                     item_id  135966
22                       tm_w   37805
14               event_name_1   33084
51           rolling_mean_180   28070
52            rolling_std_180   26630
49            rolling_mean_60   24455
50             rolling_std_60   23627
12           price_momentum_m   23602
48             rolling_std_30   20003
21                       tm_d   18382
47            rolling_mean_30   17996
44              rolling_std_7   17759
46             rolling_std_14   16901
13           price_momentum_y   15826
23                       tm_m   15803
45            rolling_mean_14   15555
43             rolling_mean_7   14969
10               item_nunique   13933
56   enc_item_id_store_id_std   11693
6                   price_std   11515
8                  price_norm   11139
24                       tm_y   11072
55  enc_item_id_store_id_mean   11015
3                  sell_price   10438
26                      tm_dw    9827

WI_2 FOODS start
195585978
15085125
15085125
[LightGBM] [Warning] Categorical features with more bins than the configured maximum bin number found.
[LightGBM] [Warning] For categorical features, max_bin and max_bin_by_feature may be ignored with a large number of categories.
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.838857
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.302203
[LightGBM] [Debug] init for col-wise cost 0.068974 seconds, init for row-wise cost 0.947851 seconds
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.207930 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Debug] Using Sparse Multi-Val Bin
[LightGBM] [Info] Total Bins 5351
[LightGBM] [Info] Number of data points in the train set: 1635889, number of used features: 57
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Debug] Re-ba

name     imp
0            item_id  126114
22              tm_w   33916
14      event_name_1   27231
51  rolling_mean_180   25515
49   rolling_mean_60   22977
52   rolling_std_180   21047
12  price_momentum_m   20613
50    rolling_std_60   19129
47   rolling_mean_30   17227
48    rolling_std_30   16351
43    rolling_mean_7   15638
21              tm_d   15419
44     rolling_std_7   15377
45   rolling_mean_14   14543
23              tm_m   14407
13  price_momentum_y   14336
46    rolling_std_14   14044
28      sales_lag_28   14037
29      sales_lag_29   13906
35      sales_lag_35   13895
42      sales_lag_42   13538
36      sales_lag_36   13368
39      sales_lag_39   13191
30      sales_lag_30   13108
40      sales_lag_40   13035

WI_3 FOODS start
195228673
15057162
15057162
[LightGBM] [Warning] Categorical features with more bins than the configured maximum bin number found.
[LightGBM] [Warning] For categorical features, max_bin and max_bin_by_feature may be ignored with a large number of categories.
[LightGBM] [Debug] Dataset::GetMultiBinFromSparseFeatures: sparse rate 0.838083
[LightGBM] [Debug] Dataset::GetMultiBinFromAllFeatures: sparse rate 0.320395
[LightGBM] [Debug] init for col-wise cost 0.069923 seconds, init for row-wise cost 0.909473 seconds
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.202303 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Debug] Using Sparse Multi-Val Bin
[LightGBM] [Info] Total Bins 5362
[LightGBM] [Info] Number of data points in the train set: 1632782, number of used features: 57
[LightGBM] [Debug] Use subset for bagging
[LightGBM] [Debug] Re-ba

name     imp
0                    item_id  133530
22                      tm_w   36916
14              event_name_1   31697
51          rolling_mean_180   27017
52           rolling_std_180   24918
12          price_momentum_m   23737
49           rolling_mean_60   22745
50            rolling_std_60   21849
48            rolling_std_30   18682
47           rolling_mean_30   17429
21                      tm_d   16814
44             rolling_std_7   16381
13          price_momentum_y   15649
46            rolling_std_14   15445
23                      tm_m   15351
45           rolling_mean_14   14409
43            rolling_mean_7   14352
10              item_nunique   13327
8                 price_norm   11723
56  enc_item_id_store_id_std   11475
28              sales_lag_28   11201
6                  price_std   11140
42              sales_lag_42   10995
36              sales_lag_36   10724
35              sales_lag_35   10536